# Find Knowledge Graph Names

In [1]:
import os
import os.path as osp
from os.path import join
from glob import glob
import random
import math
import time
from datetime import datetime

import requests

import json
import urllib
from multiprocessing.pool import ThreadPool
import threading
from urllib.request import urlopen
import urllib.request


import cv2 as cv
import pandas as pd
from scipy.io import loadmat
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt

from tqdm import tqdm_notebook as tqdm
%reload_ext autoreload
%autoreload 2
import sys
sys.path.append('/work/megapixels_dev/megapixels/')
from app.utils import file_utils, im_utils

## Load Metadata

In [2]:
dir_msceleb = '/data_store_hdd/datasets/people/msceleb/media/original/'
kg_ids_msceleb = [x.replace('m.', '/m/') for x in os.listdir(dir_msceleb)]

In [3]:
api_key = open('/work/megapixels_dev/3rdparty/knowledge-graph-api/.api_key').read()
url_kg_api = 'https://kgsearch.googleapis.com/v1/entities:search'

In [4]:
def get_kg_from_kg_obj(obj):
  # TODO detect 503 service unavailable
  timeout_error_msg = b'HTTP Error 503: Service Unavailable'
  url_error_msg = b'HTTP Error 400: Bad Request'
  global api_key, url_kg_api
  kg_id = obj['kg_id']
  params = {
      'ids': kg_id,
      'limit': 1,
      'indent': True,
      'key': api_key,
      }
  url = f'{url_kg_api}?{urllib.parse.urlencode(params)}'
  result = {'kg_id': kg_id, 'score': 0.0, 'description': '', 'url':'', 'accessed': False}  # default
  try:
    json_response = urllib.request.urlopen(url).read()
  except Exception as e:
    result['error'] = str(e)
  else:
    try:
      response = json.loads(json_response)
      items = response.get('itemListElement', [])
      result['accessed'] = True
      if items:
        item = items[0]
        item_result = item.get('result', [])
        result['description'] = item_result.get('description', '')
        det_desc = item_result.get('detailedDescription', '')
        if det_desc:
          result['description_extended'] = det_desc.get('articleBody','')
          result['description_license'] = det_desc.get('license','')
          result['description_url'] = det_desc.get('url','')
        else:
          result['description_extended'] = ''
          result['description_license'] = ''
          result['description_url'] = ''
        result_img = item_result.get('image', '')
        if result_img:
          result['image_url'] = result_img.get('contentUrl', '')
        result['name'] = item_result.get('name', '')
        result['score'] = item.get('resultScore', 0.0)
        result['url'] = item_result.get('url', '')
    except Exception as e:
      result['error'] = str(e)
  return result

In [5]:
unmapped_persons = [{'kg_id': x} for x in kg_ids_msceleb]

In [ ]:
opt_threads = 10
pbar = tqdm(total=len(unmapped_persons))

# define thread mapping function
def pool_map_persons(obj):
  global pbar
  pbar.update(1)
  kg_obj = get_kg_from_kg_obj(obj)
  return kg_obj

# convert to thread pool
mapped_persons = []
pool = ThreadPool(opt_threads)

# start threading
with tqdm(total=len(unmapped_persons)) as pbar:
  mapped_persons = pool.map(pool_map_persons, unmapped_persons)

# close tqdm
pbar.close()

```
{'@id': 'kg:/m/01008l96',
 'name': 'Mohamed Guessous',
 '@type': ['Thing', 'Person'],
 'description': 'Moroccan sociologist',
 'image': {'contentUrl': 'http://t2.gstatic.com/images?q=tbn:ANd9GcTAHGBU-4ZzSqcMbDPnSHZA10u0L9Hnppdvt_AnFdQzOYnS0aHM',
  'url': 'https://en.wikipedia.org/wiki/Mohamed_Guessous'},
 'detailedDescription': {'articleBody': 'Mohamed Guessous was a Moroccan sociologist. He was also an active politician in the Socialist Union of Popular Forces.',
  'url': 'https://en.wikipedia.org/wiki/Mohamed_Guessous',
  'license': 'https://en.wikipedia.org/wiki/Wikipedia:Text_of_Creative_Commons_Attribution-ShareAlike_3.0_Unported_License'},
 'score': 11.046742}
 ```